In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
from financial.momentum.models.kerasAdvanced import KerasAdvancedModelFactory
from financial.momentum.experiment.modelExperiment import ModelExperimentFactory
import os
from dotenv import load_dotenv
from financial.momentum.utilities import find_dotenv
from financial.momentum.utilities import metrics
import financial.data as fd
from financial.io.file.cache import FileCache
import pandas as pd
from financial.lab.experiment import Experiment
from sklearn.metrics import r2_score
from financial.model import Model

import tensorflow as tf
from keras import backend as K
import gc

def reset_gpu():
    K.clear_session()
    tf.keras.backend.clear_session()
    gc.collect()

2025-07-16 21:36:06.329499: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-16 21:36:06.443478: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752694566.487841 2820626 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752694566.501147 2820626 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1752694566.596435 2820626 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking 

In [4]:
load_dotenv(dotenv_path=find_dotenv())

cache = os.environ["CACHE"]
model_path = os.environ["MODEL"]
print(model_path)
print(os.environ["DATA"])
datastore = fd.CachedDataStore(path=os.environ["DATA"], cache=FileCache(cache_path=cache+"/"))
print(datastore) 

/home/manidmt/TFG/OTRI/models/keras
/home/manidmt/TFG/OTRI/data
CachedDataStore with 960 data sources [cache stats: {'size': 0, 'hit': 0, 'miss': 0, 'write': 0, 'read': 0, 'update': 0}]


In [12]:
ticker = "MSFT"
start_date = "1990-01-01"
end_date = "2025-06-30"

In [13]:
data = datastore.get_data(ticker, start_date, end_date)
print(data)
target = data[90 + 20:]

Date
1990-01-02      0.377807
1990-01-03      0.379936
1990-01-04      0.391110
1990-01-05      0.381532
1990-01-08      0.387385
                 ...    
2025-06-24    490.109985
2025-06-25    492.269989
2025-06-26    497.450012
2025-06-27    495.940002
2025-06-30    497.410004
Name: MSFT, Length: 8939, dtype: float64


In [7]:
factory = KerasAdvancedModelFactory()

In [8]:
from itertools import product

# Arquitecturas a probar
architectures = ["rnn", "lstm", "cnn", "cnn2d", "transformer"]

# Hiperparámetros a explorar
layer_option = [64, 32]
activation = ["relu"]
batch_size = 32
epochs = 10

def ticker_single_models(ticker):

    data = datastore.get_data(ticker, start_date, end_date)    
    target = data[90 + 20:]
    
    for arch in architectures:
        name = f"{arch}_{ticker}_{end_date[:4]}_single"

        try:
            if Model.from_file(name, path=os.environ["MODEL"]):
                print(f"⚠️ Modelo {name} ya existe. Saltando...")
                continue
        except FileNotFoundError:
            print(f"📂 Modelo {name} no existe. Procediendo a entrenar...")

        config = {
            "mode": "global",  
            "datastore": datastore,
            "ticker": ticker,
            "model_factory": factory,
            "name": name,
            "start_year": start_date,
            "end_year": end_date,
            "lookahead": 20,
            "horizon": 90,
            "model_params": {
                "architecture": arch,
                "topology": {
                    "layers": layer_option,
                    "activation": {
                        "hidden": activation,
                        "output": "linear"
                    }
                },
                "optimization": {
                    "optimizer": "adam",
                    "loss": "mean_squared_error",
                    "metrics": ["mae"],
                    "epochs": epochs,
                    "batch_size": batch_size,
                    "validation_split": 0.1
                }
            }
        }

        try:
            print("RUNNING MODEL:")
            experiment = ModelExperimentFactory.create_experiment(config)
            experiment.run()
            print("METRICS:")
            preds = experiment.reconstruct_absolute_predictions_from_relative()
            metrics(experiment, preds, target, os.environ["MODEL"])
            reset_gpu()
        except Exception as e:
            print(f"Falló el modelo {name}: {e}")

In [9]:
ticker_single_models("MSFT")
ticker_single_models("AMZN")
ticker_single_models("NVDA")

2025-07-16 21:36:25.350425: E external/local_xla/xla/stream_executor/cuda/cuda_platform.cc:51] failed call to cuInit: INTERNAL: CUDA error: Failed call to cuInit: CUDA_ERROR_UNKNOWN: unknown error
2025-07-16 21:36:25.350442: I external/local_xla/xla/stream_executor/cuda/cuda_diagnostics.cc:178] verbose logging is disabled. Rerun with verbose logging (usually --v=1 or --vmodule=cuda_diagnostics=1) to get more diagnostic output from this module
2025-07-16 21:36:25.350445: I external/local_xla/xla/stream_executor/cuda/cuda_diagnostics.cc:183] retrieving CUDA diagnostic information for host: manidmt-Katana-17-B13VGK
2025-07-16 21:36:25.350446: I external/local_xla/xla/stream_executor/cuda/cuda_diagnostics.cc:190] hostname: manidmt-Katana-17-B13VGK
2025-07-16 21:36:25.350552: I external/local_xla/xla/stream_executor/cuda/cuda_diagnostics.cc:197] libcuda reported version is: 570.133.7
2025-07-16 21:36:25.350561: I external/local_xla/xla/stream_executor/cuda/cuda_diagnostics.cc:201] kernel re

⚠️ Modelo rnn_MSFT_2025_single ya existe. Saltando...
⚠️ Modelo lstm_MSFT_2025_single ya existe. Saltando...
⚠️ Modelo cnn_MSFT_2025_single ya existe. Saltando...
⚠️ Modelo cnn2d_MSFT_2025_single ya existe. Saltando...
⚠️ Modelo transformer_MSFT_2025_single ya existe. Saltando...
⚠️ Modelo rnn_AMZN_2025_single ya existe. Saltando...
📂 Modelo lstm_AMZN_2025_single no existe. Procediendo a entrenar...
RUNNING MODEL:
Architecture: lstm
X_train before fit: (4347, 90, 1), y_train: (4347, 1)
Number of 4347 samples, 90 timesteps, 1 features
Epoch 1/300
34/34 ━━━━━━━━━━━━━━━━━━━━ 4s 90ms/step - accuracy: 6.4496e-04 - loss: 0.0325
Epoch 2/300
34/34 ━━━━━━━━━━━━━━━━━━━━ 3s 85ms/step - accuracy: 0.0010 - loss: 0.0280
Epoch 3/300
34/34 ━━━━━━━━━━━━━━━━━━━━ 3s 86ms/step - accuracy: 7.6011e-04 - loss: 0.0283
Epoch 4/300
34/34 ━━━━━━━━━━━━━━━━━━━━ 3s 86ms/step - accuracy: 0.0015 - loss: 0.0282
Epoch 5/300
34/34 ━━━━━━━━━━━━━━━━━━━━ 3s 85ms/step - accuracy: 9.0851e-04 - loss: 0.0274
Epoch 6/300
34/34 

136/136 ━━━━━━━━━━━━━━━━━━━━ 2s 16ms/step
83/83 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step
Architecture: lstm
X_train before fit: (4599, 90, 1), y_train: (4599, 1)
Number of 4599 samples, 90 timesteps, 1 features
Epoch 1/300
36/36 ━━━━━━━━━━━━━━━━━━━━ 4s 85ms/step - accuracy: 9.5540e-04 - loss: 0.0304
Epoch 2/300
36/36 ━━━━━━━━━━━━━━━━━━━━ 3s 87ms/step - accuracy: 8.1120e-04 - loss: 0.0285
Epoch 3/300
36/36 ━━━━━━━━━━━━━━━━━━━━ 3s 86ms/step - accuracy: 6.0722e-04 - loss: 0.0270
Epoch 4/300
36/36 ━━━━━━━━━━━━━━━━━━━━ 3s 87ms/step - accuracy: 8.0672e-04 - loss: 0.0281
Epoch 5/300
36/36 ━━━━━━━━━━━━━━━━━━━━ 3s 87ms/step - accuracy: 9.2543e-04 - loss: 0.0271
Epoch 6/300
36/36 ━━━━━━━━━━━━━━━━━━━━ 3s 86ms/step - accuracy: 6.8081e-04 - loss: 0.0281
Epoch 7/300
36/36 ━━━━━━━━━━━━━━━━━━━━ 3s 86ms/step - accuracy: 4.9809e-04 - loss: 0.0289
Epoch 8/300
36/36 ━━━━━━━━━━━━━━━━━━━━ 3s 87ms/step - accuracy: 7.7148e-04 - loss: 0.0267
Epoch 9/300
36/36 ━━━━━━━━━━━━━━━━━━━━ 3s 87ms/step - accuracy: 3.9214e-04 -

144/144 ━━━━━━━━━━━━━━━━━━━━ 2s 16ms/step
75/75 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step
Architecture: lstm
X_train before fit: (4851, 90, 1), y_train: (4851, 1)
Number of 4851 samples, 90 timesteps, 1 features
Epoch 1/300
38/38 ━━━━━━━━━━━━━━━━━━━━ 4s 85ms/step - accuracy: 0.0016 - loss: 0.0288
Epoch 2/300
38/38 ━━━━━━━━━━━━━━━━━━━━ 3s 88ms/step - accuracy: 8.0582e-04 - loss: 0.0270
Epoch 3/300
38/38 ━━━━━━━━━━━━━━━━━━━━ 3s 86ms/step - accuracy: 0.0013 - loss: 0.0281
Epoch 4/300
38/38 ━━━━━━━━━━━━━━━━━━━━ 3s 87ms/step - accuracy: 4.3773e-04 - loss: 0.0273
Epoch 5/300
38/38 ━━━━━━━━━━━━━━━━━━━━ 3s 85ms/step - accuracy: 0.0014 - loss: 0.0270
Epoch 6/300
38/38 ━━━━━━━━━━━━━━━━━━━━ 3s 87ms/step - accuracy: 6.7917e-04 - loss: 0.0269
Epoch 7/300
38/38 ━━━━━━━━━━━━━━━━━━━━ 3s 86ms/step - accuracy: 0.0011 - loss: 0.0264
Epoch 8/300
38/38 ━━━━━━━━━━━━━━━━━━━━ 3s 88ms/step - accuracy: 8.4151e-04 - loss: 0.0256
Epoch 9/300
38/38 ━━━━━━━━━━━━━━━━━━━━ 3s 88ms/step - accuracy: 0.0017 - loss: 0.0259
Epoch 

152/152 ━━━━━━━━━━━━━━━━━━━━ 2s 15ms/step
67/67 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step
Architecture: lstm
X_train before fit: (5102, 90, 1), y_train: (5102, 1)
Number of 5102 samples, 90 timesteps, 1 features
Epoch 1/300
40/40 ━━━━━━━━━━━━━━━━━━━━ 5s 85ms/step - accuracy: 4.9624e-04 - loss: 0.0251
Epoch 2/300
40/40 ━━━━━━━━━━━━━━━━━━━━ 3s 87ms/step - accuracy: 6.4322e-04 - loss: 0.0258
Epoch 3/300
40/40 ━━━━━━━━━━━━━━━━━━━━ 3s 87ms/step - accuracy: 0.0011 - loss: 0.0252
Epoch 4/300
40/40 ━━━━━━━━━━━━━━━━━━━━ 3s 86ms/step - accuracy: 5.8004e-04 - loss: 0.0252
Epoch 5/300
40/40 ━━━━━━━━━━━━━━━━━━━━ 4s 87ms/step - accuracy: 8.5674e-04 - loss: 0.0257
Epoch 6/300
40/40 ━━━━━━━━━━━━━━━━━━━━ 3s 86ms/step - accuracy: 6.3908e-04 - loss: 0.0258
Epoch 7/300
40/40 ━━━━━━━━━━━━━━━━━━━━ 3s 86ms/step - accuracy: 0.0010 - loss: 0.0266
Epoch 8/300
40/40 ━━━━━━━━━━━━━━━━━━━━ 3s 85ms/step - accuracy: 3.9645e-04 - loss: 0.0249
Epoch 9/300
40/40 ━━━━━━━━━━━━━━━━━━━━ 3s 87ms/step - accuracy: 0.0014 - loss: 0.025

...

205/205 ━━━━━━━━━━━━━━━━━━━━ 3s 15ms/step
205/205 ━━━━━━━━━━━━━━━━━━━━ 3s 14ms/step
METRICS:
Falló el modelo lstm_NVDA_2025_single: Found input variables with inconsistent numbers of samples: [8829, 6540]
📂 Modelo cnn_NVDA_2025_single no existe. Procediendo a entrenar...
RUNNING MODEL:
Architecture: cnn
Epoch 1/300
31/31 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0026 - loss: 0.3691
Epoch 2/300
31/31 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0021 - loss: 0.0498
Epoch 3/300
31/31 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 9.6589e-04 - loss: 0.0399
Epoch 4/300
31/31 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0011 - loss: 0.0406
Epoch 5/300
31/31 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0010 - loss: 0.0384    
Epoch 6/300
31/31 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0010 - loss: 0.0355    
Epoch 7/300
31/31 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0013 - loss: 0.0391
Epoch 8/300
31/31 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0015 - loss: 0.0375
Epo

123/123 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step  
83/83 ━━━━━━━━━━━━━━━━━━━━ 0s 980us/step
Architecture: cnn
Epoch 1/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 5.9464e-04 - loss: 0.4583
Epoch 2/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.0016 - loss: 0.0473
Epoch 3/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.0014 - loss: 0.0379
Epoch 4/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0014 - loss: 0.0356
Epoch 5/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0029 - loss: 0.0373
Epoch 6/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.0015 - loss: 0.0370
Epoch 7/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.0026 - loss: 0.0348
Epoch 8/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0015 - loss: 0.0357
Epoch 9/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0017 - loss: 0.0354
Epoch 10/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0016 - loss: 0.0367
Epoch 11/300
33/33 ━━━━━━━━━━━━━━━━━━━━ 0s 

131/131 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step  
75/75 ━━━━━━━━━━━━━━━━━━━━ 0s 975us/step
Architecture: cnn
Epoch 1/300
35/35 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 6.4532e-04 - loss: 0.3540
Epoch 2/300
35/35 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0024 - loss: 0.0395
Epoch 3/300
35/35 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 8.7647e-04 - loss: 0.0355
Epoch 4/300
35/35 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.0021 - loss: 0.0341
Epoch 5/300
35/35 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.0021 - loss: 0.0348
Epoch 6/300
35/35 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0010 - loss: 0.0373    
Epoch 7/300
35/35 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0012 - loss: 0.0377
Epoch 8/300
35/35 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.0010 - loss: 0.0372    
Epoch 9/300
35/35 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.0010 - loss: 0.0356    
Epoch 10/300
35/35 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.0018 - loss: 0.0371
Epoch 11/300
35/35 ━━━━━━━━

139/139 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step  
67/67 ━━━━━━━━━━━━━━━━━━━━ 0s 941us/step
Architecture: cnn
Epoch 1/300
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0014 - loss: 0.3880
Epoch 2/300
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 5.4237e-04 - loss: 0.0397
Epoch 3/300
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 8.3108e-04 - loss: 0.0326
Epoch 4/300
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 7.7445e-04 - loss: 0.0340
Epoch 5/300
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0029 - loss: 0.0342
Epoch 6/300
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 5.7504e-04 - loss: 0.0341
Epoch 7/300
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 8.1186e-04 - loss: 0.0338
Epoch 8/300
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 4.3659e-04 - loss: 0.0321
Epoch 9/300
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 8.6153e-04 - loss: 0.0362
Epoch 10/300
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.0012 - loss: 0.0371
Epoch 11/300
37/37 

KeyboardInterrupt: 

In [ ]:
index_tickers = [
    "^GSPC",          # S&P 500
    "^IXIC",          # Nasdaq
    "^DJI",           # Dow Jones Industrial Average
    "^FTSE",          # FTSE 100
    "^N225",          # Nikkei 225
    "^IBEX",          # Ibex 35
]

In [ ]:
for ticker in index_tickers:
    ticker_single_models(ticker)